In [1]:
# This file deletes in the pipeline the unwanted relationship by different rules
import pandas as pd
import sqlite3
import numpy as np


CONN = sqlite3.connect('../../Assets/Dataset/Tmp/dataset2.db')

def get_RDF() -> pd.DataFrame:
    """
    QUERY = "SELECT * FROM RDFs " \
    "INNER JOIN Subjects USING (SubjectID) " \
    "INNER JOIN Relationships USING (RelationshipID) " \
    "INNER JOIN Objects USING (ObjectID);"
    RDF = pd.read_sql_query(QUERY, CONN)
    RDF = RDF[["SubjectURI", "RelationshipURI", "ObjectURI"]]
    RDF = RDF.dropna()
    """
    Subjects = pd.read_sql_query('SELECT * FROM Subjects;', CONN)
    Objects = pd.read_sql_query('SELECT * FROM Objects;', CONN)
    Relationships = pd.read_sql_query('SELECT * FROM Relationships;', CONN)
    RDF = pd.read_sql_query('SELECT * FROM RDFs;', CONN)

    # drop '' values 
    Subjects = Subjects.replace('', np.nan)# .dropna()
    Relationships = Relationships.replace('', np.nan)# .dropna()
    Objects = Objects.replace('', np.nan)# .dropna()

    # join RDF with its components
    RDF = RDF.merge(Subjects, left_on="SubjectID", right_on="SubjectID")
    RDF = RDF.merge(Objects, left_on="ObjectID", right_on="ObjectID")
    RDF = RDF.merge(Relationships, left_on="RelationshipID", right_on="RelationshipID")
    RDF = RDF[["SubjectURI", "RelationshipURI", "ObjectURI", "MovieID"]]
    return RDF


#def delete_relationship_by_uri(RDF: pd.DataFrame, )

def delete_relationship_by_uri(RDF: pd.DataFrame, uri: str) -> pd.DataFrame:
    return RDF[RDF["RelationshipURI"]!= uri]



RDF = get_RDF()
# RDF = RDF.dropna()
# print(RDF)


In [2]:
def filter_by_frequence_relationship_uri(RDF: pd.DataFrame, count_treshold) -> pd.DataFrame:
    counts = RDF["RelationshipURI"].value_counts() 
    RDF["RelationshipFreq"] = RDF["RelationshipURI"].map(counts)
    RDF = RDF[RDF["RelationshipFreq"] >= count_treshold]
    # counts is a series as key: relationship, value: count
    # counts = counts[counts > count_treshold]
    # relationships = counts.index
    # RDF = RDF[RDF["RelationshipURI"].isin(relationships)]
    # RDF = RDF.groupby("RelationshipURI").filter(lambda x: len(x) >= count_treshold)
    return RDF

RDF = filter_by_frequence_relationship_uri(RDF, 1)
# print(new_RDF)



In [ ]:
def filter_by_frequence_movie_id(RDF: pd.DataFrame, min_treshold, max_treshold) -> pd.DataFrame:
    counts = RDF["MovieID"].value_counts() 
    RDF["MovieFreq"] = RDF["MovieID"].map(counts)
    RDF = RDF[RDF["MovieFreq"] >= min_treshold]
    RDF = RDF[RDF["MovieFreq"] < max_treshold]
    # counts is a series as key: relationship, value: count
    # counts = counts[counts > count_treshold]
    # relationships = counts.index
    # RDF = RDF[RDF["RelationshipURI"].isin(relationships)]
    # RDF = RDF.groupby("RelationshipURI").filter(lambda x: len(x) >= count_treshold)
    return RDF

RDF = filter_by_frequence_movie_id(RDF, 1, 1500)
print(RDF)

                                                 SubjectURI  \
0             http://dbpedia.org/resource/Nights_of_Cabiria   
1         http://dbpedia.org/resource/California_Science...   
2                 http://dbpedia.org/resource/China_Captain   
3         http://dbpedia.org/resource/Caravan_of_Courage...   
4                http://dbpedia.org/resource/WHIH_Newsfront   
...                                                     ...   
12725500   http://dbpedia.org/resource/I_Will_Follow_(film)   
12725501   http://dbpedia.org/resource/I_Will_Follow_(film)   
12725502  http://dbpedia.org/resource/I_Witnessed_Genoci...   
12725503  http://dbpedia.org/resource/I_Woke_Up_Early_th...   
12725504           http://dbpedia.org/resource/I_Won't_Play   

                                       RelationshipURI  \
0          http://www.w3.org/2002/07/owl#differentFrom   
1          http://www.w3.org/2002/07/owl#differentFrom   
2          http://www.w3.org/2002/07/owl#differentFrom   
3          